In [ ]:
import time

from scipy.optimize import minimize, Bounds
import numpy as np
import pandas as pd

# Display all rows.
pd.set_option('display.max_rows', None)

from flow import Flow
from pump import Pump
from plot import plot_results
from setup import *

## Pumps

In [ ]:
# Head (m)
IHEAD = 10
IHEAD = 1
OHEAD = 2

ISHAPE = 0.95
OSHAPE = 0.35

ipump = Pump(IBEP, IHEAD, 0.75, 0.25, ISHAPE)
opump = Pump(OBEP, OHEAD, 0.75, 0.25, OSHAPE)

In [ ]:
ipump.plot(0, 4)

In [ ]:
opump.plot(0, 35)

## Bounds

In [ ]:
# Could impose flow bounds based on energy considerations.
# bounds = Bounds([ipump.flow_min, opump.flow_min], [ipump.flow_max, opump.flow_max])
# But for consistency just use the same bounds as the global optimisation problems.
bounds = Bounds([INPUT_FLOW_MIN, OUTPUT_FLOW_MIN], [INPUT_FLOW_MAX, OUTPUT_FLOW_MAX])

## Constraints

In [ ]:
def tank_constraint(x):
    """
    Will return a negative value if the tank either (1) overflows or (2) underflows.

    Since these two conditions are mutually exclusive we can combine this into a single constraint.
    """
    iflow, oflow = x
    
    levels = tank.update(iflow - oflow, dt, False)
    
    return min(tank.capacity - levels, levels)

In [ ]:
constraints = [
    {"type": "ineq", "fun": tank_constraint},
]

## Optimisation

In [ ]:
def callback(x, *args, **kwargs):
    """
    A function that will run after each optimisation iteration.
    """
    for i, con in enumerate(constraints):
        value = con["fun"](x)
        if con["type"] == "ineq":
            violated = value < 0
        elif con["type"] == "eq":
            violated = abs(value) >= 1e-6
        
        status = '🛑' if violated else '✅'
        
        print(f"{i} {status} ({con["type"]:4}): {value:+.2e}")

In [ ]:
def objective(x):
    iflow, oflow = x
    
    return (
        WEIGHT_TANK_LEVEL * (tank.capacity - tank.update(iflow - oflow, dt, False)) +
        WEIGHT_DEMAND * (demand - oflow) ** 2
    )

In [ ]:
SOLVER = "trust-constr"
extra_options = {
    'maxiter': 10000,
    "verbose": 2
}

# SOLVER = 'SLSQP'
# extra_options = {
#     'maxiter': 1000,
# }

In [ ]:
def optimization(dt, x0):
    result = minimize(
        objective,
        x0.tuple,
        bounds=bounds,
        constraints=constraints,    
        callback=callback,
        options={
            'disp': True,
            **extra_options
        },
        method=SOLVER,
    )

    return Flow(*result.x)

In [ ]:
# Initial guesses.
x = Flow(0, 0)

start = time.perf_counter()

for t in range(time_steps):
    print(f"time: {TIMES[t]} =============================================================")
    demand = DEMAND[t]

    x = optimization(dt, x)

    tank.update(x.p_in - x.p_out, dt)
    ipump.run(x.p_in, dt)
    opump.run(x.p_out, dt)

    if t < time_steps - 1:
        ipower = ipump.power_consumed(x.p_in)
        opower = opump.power_consumed(x.p_out)
        print(f"Level:          {tank.level}")
        print(f"Flow (input):   {x.p_in}")
        print(f"Flow (output):  {x.p_out}")
        print(f"Power (input):  {ipower}")
        print(f"Power (output): {opower}")

end = time.perf_counter()

In [ ]:
print(f"Time: {end - start:.6f} seconds")

In [ ]:
results = pd.DataFrame({
    "time": TIMES,
    "demand": DEMAND,
    "inflow": ipump.flows,
    "outflow": opump.flows,
    "level": tank.levels[1:],
    "ienergy": ipump.energy_consumed,
    "oenergy": opump.energy_consumed,
})
results["energy"] = results.ienergy + results.oenergy

In [ ]:
plt = plot_results(results)

plt.savefig(f"tank-sequential-scipy-solution-{str(SOLVER).lower()}.png", format="png", dpi=300)

plt.show()